# 背景差分

## 目的
このチュートリアルでは

* 背景差分について学ぶ．

## 基礎
背景差分はComputer Visionを基にしたアプリケーションにおけるよく使われる前処理の内の一つである．例えば，固定カメラによる来客者数・退室者数の測定，屋外カメラを使った交通流計測などが挙げられる．このようなアプリケーションを実現するために，まず初めに画像中に写る人や車のみを検出する必要がある．技術的には，静的背景から移動物体を検出する問題を解かなければならない．

背景のみが写った画像が手に入れば問題は簡単である．移動物体が写っている画像から背景画像を引き算すれば十分だからである．しかし，ほとんどの場合，そのような背景画像を取得できないため，どのような画像が手元にあるにせよ，背景を抽出する必要が生じる．車の影が写ると更に問題は複雑になる．なぜなら影もまた移動するため，単純な引き算では影も前景物体とみなされてしまうからである．

このような目的のために，様々なアルゴリズムが提案されてきた．OpenCVは簡単に使える3つのアルゴリズムを用意している．一つ一つ紹介していこう．

## BackgroundSubtractorMOG
これは混合正規分布(Gaussian Mixture)を基にした前景・背景の領域分割アルゴリズムで，P. KadewTraKuPongとR. Bowdenが2001年に発表した論文 “An improved adaptive background mixture model for real-time tracking with shadow detection” で提案された．背景に属する各画素を混合数(K)が3から5までの混合分布でモデル化する手法である．混合分布の重みはシーン中に対応する色が存在している時間の割合を表している．可能性の高い背景色は長く留まり，より静的になる．

実装する上で， [cv2.bgsegm.createBackgroundSubtractorMOG({, history{, nmixtures{, backgroundRatio{, noiseSigma}}}})](http://docs.opencv.org/3.0-beta/modules/video/doc/motion_analysis_and_object_tracking.html?highlight=createbackgroundsubtractormog#cv2.createBackgroundSubtractorMOG) 関数を使って背景オブジェクトを作成する（注意: OpenCV2では`cv2.createBackgroundSubtractorMOG()`関数）． 履歴の長さ(history)，混合数(nmixtures)，しきい値(backgroundRatio)などオプション指定のパラメータがあるが，それぞれデフォルト値は決まっている．背景オブジェクトを作成したら，それ以降は画像を撮影する度に `backgroundsubtractor.apply()` 関数を使って前景領域のマスクを取得する．

以下に示した簡単な例を見てみよう:([使用している動画](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/test.avi))

In [1]:
import numpy as np
import cv2

cap = cv2.VideoCapture('test.avi')

fgbg = cv2.bgsegm.createBackgroundSubtractorMOG()

while(1):
    ret, frame = cap.read()

    fgmask = fgbg.apply(frame)

    cv2.imshow('frame',fgmask)
    k = cv2.waitKey(30) & 0xff
    if k == 27:
        break

cap.release()
cv2.destroyAllWindows()
for _ in range(5):
    cv2.waitKey(1)

(この例も含めた全てのデモプログラムの結果は，このページの一番下にまとめて表示する)

## BackgroundSubtractorMOG2
このアルゴリズムも混合正規分布を基にした前景・背景の領域分割アルゴリズムである．Z.Zivkovicが2004年に発表した論文 “Improved adaptive Gaussian mixture model for background subtraction” と2006年に発表した “Efficient Adaptive Density Estimation per Image Pixel for the Task of Background Subtraction” を基にしている．このアルゴリズムの重要な点は，画素毎に最適な混合数を選択する点である(前の例ではアルゴリズムを通してK個のガウス分布(正規分布)を使っていた点を思い出そう)．照明の変化などの動的なシーンに対する適応力が優れている．

前の例と同様に[cv2.createBackgroundSubtractorMOG2({, history{, varThreshold{, detectShadows}}})](http://docs.opencv.org/3.2.0/de/de1/group__video__motion.html#ga2beb2dee7a073809ccec60f145b6b29c)関数によって背景オブジェクトを作成する．ここでは影の検出を行うか否かを選択するオプション(`detectShadows`)がある．もしも `detectShadows = True` とすれば影を検出できるが，計算速度は遅くなってしまう(デフォルトはこの値)。影は灰色で描画される: ([使用している動画](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/test.avi))

In [3]:
import numpy as np
import cv2

cap = cv2.VideoCapture('test.avi')

fgbg = cv2.createBackgroundSubtractorMOG2()

while(1):
    ret, frame = cap.read()

    fgmask = fgbg.apply(frame)

    cv2.imshow('frame',fgmask)
    k = cv2.waitKey(30) & 0xff
    if k == 27:
        break

cap.release()
cv2.destroyAllWindows()
for _ in range(5):
    cv2.waitKey(1)

(この例も含めた全てのデモプログラムの結果は，このページの一番下にまとめて表示する)

## BackgroundSubtractorGMG
このアルゴリズムは統計的な背景の推定法と画素単位でのベイス推定に基づく領域分割を組み合わせたアルゴリズムである．Andrew B. Godbehere, Akihiro Matsukawa, Ken Goldberg が2012年に発表した論文 “Visual Tracking of Human Visitors under Variable-Lighting Conditions for a Responsive Audio Art Installation” で提案されたアルゴリズムである．論文にあるように，サンフランシスコのContemporary Jewish Museumで2011年3月31日から7月31日の期間 “Are We There Yet?” というインタラクティブ オーディオ アートの展示で使われた．

背景のモデル構築に最初の数フレーム(デフォルトで120)を使いる．ベイズ推定を使って前景物体である可能性を識別する確率的前景領域抽出アルゴリズムを使いる．推定は適応的であり，照明変化に対する適応力を上げるために，古い画像より新しい画像を重視する．クロージングやオープニングといったモーフォロジー処理を行いノイズを削除する．最初の数フレームの間は背景モデルを作成するため，真っ黒なウィンドウが表示される．

ノイズを消すには，モーフォロジー処理を適用すると良いだろう: ([使用している動画](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/test.avi))

In [4]:
import numpy as np
import cv2

cap = cv2.VideoCapture('test.avi')

kernel = cv2.getStructuringElement(cv2.MORPH_ELLIPSE,(3,3))
fgbg = cv2.bgsegm.createBackgroundSubtractorGMG()

while(1):
    ret, frame = cap.read()

    fgmask = fgbg.apply(frame)
    fgmask = cv2.morphologyEx(fgmask, cv2.MORPH_OPEN, kernel)

    cv2.imshow('frame',fgmask)
    k = cv2.waitKey(30) & 0xff
    if k == 27:
        break

cap.release()
cv2.destroyAllWindows()
for _ in range(5):
    cv2.waitKey(1)

## 結果

* 原画像

以下の画像は入力動画像中の200フレーム目の映像である．
![](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/_images/resframe.jpg)

* BackgroundSubtractorMOGの結果
![](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/_images/resmog.jpg)

* BackgroundSubtractorMOG2の結果

灰色の領域は影領域を表している．![](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/_images/resmog2.jpg)

* BackgroundSubtractorGMGの結果

モーフォロジカル処理によってノイズが除去されている． ![](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/_images/resgmg.jpg)

## 補足資料
1. KadewTraKuPong, K. & Bowden R. (2001) “[An improved adaptive background mixture model for real-time tracking with shadow detection](http://personal.ee.surrey.ac.uk/Personal/R.Bowden/publications/avbs01/avbs01.pdf)”. In Proc. 2nd European Workshop on Advanced Video Based Surveillance Systems, AVBS01.

2. Zivkovic, Z. (2004). “[Improved adaptive Gausian mixture model for background subtraction](http://ieeexplore.ieee.org/stamp/stamp.jsp?arnumber=1333992)”. In Proceedings of the 17th International Conference on Pattern Recognition (ICPR’04), Vol. 2. pp.28-31.

3. Zivkovic, Z. & van der Heijden, F.(2006). “[Efficient Adaptive Density Estimation per Image Pixel for the Task of Background Subtraction](http://www.zoranz.net/Publications/zivkovicPRL2006.pdf)”. Pattern Recognition Letters. 27(7). 773-780.

4. Godbehere, A. B., Matsukawa, A. & Goldberg, K. (2012) “[Visual Tracking of Human Visitors under Variable-Lighting Conditions for a Responsive Audio Art Installation](http://goldberg.berkeley.edu/pubs/acc-2012-visual-tracking-final.pdf)”. In American Control Conference (ACC) 2012.

